In [2]:
from env.balancebot_env import BalancebotEnv
from stable_baselines import PPO2
from stable_baselines.common.policies import ActorCriticPolicy, FeedForwardPolicy
from stable_baselines.common.vec_env import DummyVecEnv
from stable_baselines.common.vec_env import SubprocVecEnv
from stable_baselines.bench import Monitor
from stable_baselines.a2c.utils import linear

import os
import time
import torch
import tensorflow as tf
import numpy as np

/home/kazami/.local/share/virtualenvs/pybullet-example-1Lt2_XSQ/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/kazami/.local/share/virtualenvs/pybullet-example-1Lt2_XSQ/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/kazami/.local/share/virtualenvs/pybullet-example-1Lt2_XSQ/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint

In [3]:
log_dir = "/tmp/gym/{}".format(int(time.time()))
os.makedirs(log_dir, exist_ok=True)

In [4]:
import sys
print(sys.path)
import numpy



['/home/kazami/workspace/pybullet-example', '/home/kazami/workspace/caffe2/build', '/home/kazami/workspace/pybullet-example', '/home/kazami/.pyenv/versions/3.7.0/lib/python37.zip', '/home/kazami/.pyenv/versions/3.7.0/lib/python3.7', '/home/kazami/.pyenv/versions/3.7.0/lib/python3.7/lib-dynload', '', '/home/kazami/.local/share/virtualenvs/pybullet-example-1Lt2_XSQ/lib/python3.7/site-packages', '/home/kazami/.local/share/virtualenvs/pybullet-example-1Lt2_XSQ/lib/python3.7/site-packages/IPython/extensions', '/home/kazami/.ipython']


In [5]:
# Create the environment
def make_env(rank):
    def _init():
        env = BalancebotEnv(render=False)
        env = Monitor(env, os.path.join(log_dir, str(rank)))
        return env
    return _init

num_cpu = 16
env = SubprocVecEnv([make_env(rank=i) for i in range(num_cpu)])


In [6]:
def const_linear(input_tensor, scope, np_w, np_b):
    in_shape = input_tensor.get_shape().as_list()
    n_input = in_shape[1]
    assert n_input == np_w.shape[0], \
        f"incompatible weight shape: {in_shape} and {np_w.shape}"
    n_output = np_w.shape[1]
    assert n_output == np_b.shape[0], \
        f'incompatible bias shape: {np_w.shape} and {np_b.shape}'
    with tf.variable_scope(scope):
        tf_w = tf.constant(np_w, name='w', dtype=input_tensor.dtype)
        tf_b = tf.constant(np_b, name='b', dtype=input_tensor.dtype)
        return tf.matmul(input_tensor, tf_w) + tf_b

In [7]:
# Create the RL Agwnt
class CustomPolicy2(ActorCriticPolicy):
    np_pi_w = None
    np_pi_b = None
    np_vf_w = None
    np_vf_b = None
    var_layers = [16]
    
    def __init__(self, sess, ob_space, ac_space, n_env, n_steps, n_batch, reuse=False):
        super(CustomPolicy, self).__init__(sess, ob_space, 
                                           ac_space, n_env, n_steps, 
                                           n_batch, n_lstm=256,
                                           reuse=reuse, scale=False)
        if any([self.np_pi_w is None,
                self.np_pi_b is None,
                self.np_vf_w is None,
                self.np_vf_b is None]):
            raise ValueError('Run CustomPolicy.set_weights first before using this CustomPolicy')
        with tf.variable_scope('model', reuse=reuse):
            activ = tf.tanh
            processed_x = tf.layers.flatten(self.processed_x)
            pi_h = activ(const_linear(processed_x, 'pi_fc0', self.np_pi_w, self.np_pi_b))
            vf_h = activ(const_linear(processed_x, 'vf_fc0', self.np_vf_w, self.np_vf_b))
            for i, layer_size in enumerate(self.var_layers, 1):
                pi_h = activ(linear(pi_h, 'pi_fc' + str(i), n_hidden=layer_size, init_scale=np.sqrt(2)))
                vf_h = activ(linear(vf_h, 'vf_fc' + str(i), n_hidden=layer_size, init_scale=np.sqrt(2)))
            value_fn = linear(vf_h, 'vf', 1)
            pi_latent = pi_h
            vf_latent = vf_h

            self.proba_distribution, self.policy, self.q_value = \
                self.pdtype.proba_distribution_from_latent(pi_latent, vf_latent, init_scale=0.01)

        self.value_fn = value_fn
        self.initial_state = None
        self._setup_init()
    
    def step(self, obs, state=None, mask=None, deterministic=False):
        if deterministic:
            action, value, neglogp = self.sess.run([self.deterministic_action, self._value, self.neglogp],
                                                   {self.obs_ph: obs})
        else:
            action, value, neglogp = self.sess.run([self.action, self._value, self.neglogp],
                                                   {self.obs_ph: obs})
        return action, value, self.initial_state, neglogp

    def proba_step(self, obs, state=None, mask=None):
        return self.sess.run(self.policy_proba, {self.obs_ph: obs})

    def value(self, obs, state=None, mask=None):
        return self.sess.run(self._value, {self.obs_ph: obs})
    
    @classmethod
    def custom_set_weights(cls, np_pi_w, np_pi_b, np_vf_w, np_vf_b, var_layers=None):
        cls.np_pi_w = np_pi_w
        cls.np_pi_b = np_pi_b
        cls.np_vf_w = np_vf_w
        cls.np_vf_b = np_vf_b
        if var_layers:
            cls.var_layers = var_layers

In [8]:
# put your pytorch numpy weights here
CustomPolicy2.custom_set_weights(np.random.rand(4, 32), np.random.rand(32),
                                np.random.rand(4, 32), np.random.rand(32))

In [9]:
class CustomPolicy(FeedForwardPolicy):
    def __init__(self, *args, **kwargs):
        super(CustomPolicy, self).__init__(*args, **kwargs,
                                           layers=[32, 16],
                                           feature_extraction="mlp")

In [9]:
model = PPO2(CustomPolicy, env, verbose=1, tensorboard_log=log_dir+"/tensorboard")





Instructions for updating:
Use keras.layers.flatten instead.


Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where




In [10]:
observation_dim = env.observation_space.shape[0]

In [11]:
weight_encoder = torch.rand(observation_dim, 32,requires_grad=False).numpy()

In [12]:
weight_encoder.shape

(8, 32)

## How do I put the weight of encoder into model ?
## I want to put the weight into 'pi_fc0' and 'vf_fc0' and set them to untrainable
 

![Network](assets/network.png)

In [13]:
# Train and Save the agent
model.learn(total_timesteps=2e7, tb_log_name="PPO2")
model.save("ppo_save")


---------------------------------------
| approxkl           | 1.2240451e-05  |
| clipfrac           | 0.0            |
| explained_variance | -0.00497       |
| fps                | 1966           |
| n_updates          | 1              |
| policy_entropy     | 1.4191945      |
| policy_loss        | -0.00013972183 |
| serial_timesteps   | 128            |
| time_elapsed       | 0.000411       |
| total_timesteps    | 2048           |
| value_loss         | 96.03353       |
---------------------------------------
--------------------------------------
| approxkl           | 8.8888355e-06 |
| clipfrac           | 0.0           |
| ep_len_mean        | 248           |
| ep_reward_mean     | 124           |
| explained_variance | 0.00253       |
| fps                | 2824          |
| n_updates          | 2             |
| policy_entropy     | 1.4190385     |
| policy_loss        | -9.016643e-05 |
| serial_timesteps   | 256           |
| time_elapsed       | 1.04          |
| total_tim

---------------------------------------
| approxkl           | 1.9321224e-06  |
| clipfrac           | 0.0            |
| ep_len_mean        | 341            |
| ep_reward_mean     | 218            |
| explained_variance | 0.039          |
| fps                | 2757           |
| n_updates          | 15             |
| policy_entropy     | 1.4291987      |
| policy_loss        | -5.1390234e-05 |
| serial_timesteps   | 1920           |
| time_elapsed       | 11.4           |
| total_timesteps    | 30720          |
| value_loss         | 54.03569       |
---------------------------------------
--------------------------------------
| approxkl           | 1.9730742e-06 |
| clipfrac           | 0.0           |
| ep_len_mean        | 345           |
| ep_reward_mean     | 222           |
| explained_variance | 0.0309        |
| fps                | 2937          |
| n_updates          | 16            |
| policy_entropy     | 1.4286892     |
| policy_loss        | -6.116342e-05 |
| serial_t

---------------------------------------
| approxkl           | 3.4354848e-06  |
| clipfrac           | 0.0            |
| ep_len_mean        | 351            |
| ep_reward_mean     | 228            |
| explained_variance | 0.0198         |
| fps                | 3010           |
| n_updates          | 29             |
| policy_entropy     | 1.4280437      |
| policy_loss        | -5.6695775e-05 |
| serial_timesteps   | 3712           |
| time_elapsed       | 21.5           |
| total_timesteps    | 59392          |
| value_loss         | 56.073227      |
---------------------------------------
--------------------------------------
| approxkl           | 8.133121e-07  |
| clipfrac           | 0.0           |
| ep_len_mean        | 359           |
| ep_reward_mean     | 235           |
| explained_variance | 0.0319        |
| fps                | 3028          |
| n_updates          | 30            |
| policy_entropy     | 1.4275141     |
| policy_loss        | 1.8750405e-05 |
| serial_t

---------------------------------------
| approxkl           | 8.042181e-06   |
| clipfrac           | 0.0            |
| ep_len_mean        | 344            |
| ep_reward_mean     | 220            |
| explained_variance | 0.0547         |
| fps                | 2803           |
| n_updates          | 43             |
| policy_entropy     | 1.434556       |
| policy_loss        | -0.00019516991 |
| serial_timesteps   | 5504           |
| time_elapsed       | 31.2           |
| total_timesteps    | 88064          |
| value_loss         | 58.670227      |
---------------------------------------
---------------------------------------
| approxkl           | 3.0809206e-05  |
| clipfrac           | 0.0            |
| ep_len_mean        | 346            |
| ep_reward_mean     | 223            |
| explained_variance | 0.0348         |
| fps                | 2618           |
| n_updates          | 44             |
| policy_entropy     | 1.4349147      |
| policy_loss        | -0.00039868712 |


---------------------------------------
| approxkl           | 1.1651409e-06  |
| clipfrac           | 0.0            |
| ep_len_mean        | 339            |
| ep_reward_mean     | 216            |
| explained_variance | 0.2            |
| fps                | 2939           |
| n_updates          | 57             |
| policy_entropy     | 1.4327381      |
| policy_loss        | -2.8653885e-06 |
| serial_timesteps   | 7296           |
| time_elapsed       | 41.3           |
| total_timesteps    | 116736         |
| value_loss         | 42.262363      |
---------------------------------------
---------------------------------------
| approxkl           | 1.6865957e-06  |
| clipfrac           | 0.0            |
| ep_len_mean        | 339            |
| ep_reward_mean     | 216            |
| explained_variance | 0.214          |
| fps                | 2944           |
| n_updates          | 58             |
| policy_entropy     | 1.4326534      |
| policy_loss        | -5.0360715e-05 |


...

-------------------------------------
| approxkl           | 0.0052222265 |
| clipfrac           | 0.056274414  |
| ep_len_mean        | 5.18e+03     |
| ep_reward_mean     | 4.94e+03     |
| explained_variance | 0.418        |
| fps                | 2633         |
| n_updates          | 9692         |
| policy_entropy     | 1.3791133    |
| policy_loss        | 0.0016774096 |
| serial_timesteps   | 1240576      |
| time_elapsed       | 6.77e+03     |
| total_timesteps    | 19849216     |
| value_loss         | 0.0023951079 |
-------------------------------------
-------------------------------------
| approxkl           | 0.012637285  |
| clipfrac           | 0.15039062   |
| ep_len_mean        | 5.18e+03     |
| ep_reward_mean     | 4.94e+03     |
| explained_variance | 0.462        |
| fps                | 2977         |
| n_updates          | 9693         |
| policy_entropy     | 1.3781949    |
| policy_loss        | 0.0050496194 |
| serial_timesteps   | 1240704      |
| time_elaps

-------------------------------------
| approxkl           | 0.0057860734 |
| clipfrac           | 0.07421875   |
| ep_len_mean        | 5.18e+03     |
| ep_reward_mean     | 4.94e+03     |
| explained_variance | 0.255        |
| fps                | 3016         |
| n_updates          | 9707         |
| policy_entropy     | 1.3793309    |
| policy_loss        | 0.0036019864 |
| serial_timesteps   | 1242496      |
| time_elapsed       | 6.78e+03     |
| total_timesteps    | 19879936     |
| value_loss         | 0.0010389001 |
-------------------------------------
-------------------------------------
| approxkl           | 0.0058043236 |
| clipfrac           | 0.07397461   |
| ep_len_mean        | 5.18e+03     |
| ep_reward_mean     | 4.94e+03     |
| explained_variance | 0.405        |
| fps                | 3057         |
| n_updates          | 9708         |
| policy_entropy     | 1.3788825    |
| policy_loss        | 0.0009639493 |
| serial_timesteps   | 1242624      |
| time_elaps

---------------------------------------
| approxkl           | 0.0029047362   |
| clipfrac           | 0.030273438    |
| ep_len_mean        | 5.18e+03       |
| ep_reward_mean     | 4.94e+03       |
| explained_variance | 0.377          |
| fps                | 3001           |
| n_updates          | 9722           |
| policy_entropy     | 1.362572       |
| policy_loss        | -0.00014779848 |
| serial_timesteps   | 1244416        |
| time_elapsed       | 6.79e+03       |
| total_timesteps    | 19910656       |
| value_loss         | 0.0016527924   |
---------------------------------------
-------------------------------------
| approxkl           | 0.0066111    |
| clipfrac           | 0.08215332   |
| ep_len_mean        | 5.18e+03     |
| ep_reward_mean     | 4.94e+03     |
| explained_variance | 0.328        |
| fps                | 3020         |
| n_updates          | 9723         |
| policy_entropy     | 1.3606887    |
| policy_loss        | 0.0015072939 |
| serial_timesteps  

-------------------------------------
| approxkl           | 0.005144561  |
| clipfrac           | 0.060791016  |
| ep_len_mean        | 5.18e+03     |
| ep_reward_mean     | 4.94e+03     |
| explained_variance | 0.424        |
| fps                | 2932         |
| n_updates          | 9737         |
| policy_entropy     | 1.347745     |
| policy_loss        | 0.0005460853 |
| serial_timesteps   | 1246336      |
| time_elapsed       | 6.8e+03      |
| total_timesteps    | 19941376     |
| value_loss         | 0.002462529  |
-------------------------------------
---------------------------------------
| approxkl           | 0.0069145733   |
| clipfrac           | 0.09484863     |
| ep_len_mean        | 5.18e+03       |
| ep_reward_mean     | 4.94e+03       |
| explained_variance | 0.499          |
| fps                | 2972           |
| n_updates          | 9738           |
| policy_entropy     | 1.3460333      |
| policy_loss        | -0.00077445665 |
| serial_timesteps   | 1246464

--------------------------------------
| approxkl           | 0.0046411213  |
| clipfrac           | 0.057006836   |
| ep_len_mean        | 5.18e+03      |
| ep_reward_mean     | 4.94e+03      |
| explained_variance | 0.564         |
| fps                | 2532          |
| n_updates          | 9752          |
| policy_entropy     | 1.3346069     |
| policy_loss        | -0.0006790141 |
| serial_timesteps   | 1248256       |
| time_elapsed       | 6.81e+03      |
| total_timesteps    | 19972096      |
| value_loss         | 0.004132092   |
--------------------------------------
---------------------------------------
| approxkl           | 0.0047413735   |
| clipfrac           | 0.05883789     |
| ep_len_mean        | 5.18e+03       |
| ep_reward_mean     | 4.94e+03       |
| explained_variance | 0.567          |
| fps                | 2996           |
| n_updates          | 9753           |
| policy_entropy     | 1.3344221      |
| policy_loss        | -0.00028844448 |
| serial_timest

In [14]:
log_dir+"/tensorboard/"

'/tmp/gym/1591954108/tensorboard/'

## You can open tensorboard at terminal
## For example:
### tensorboard --logdir log_dir+"/tensorboard"

In [10]:
# delete trained model to demonstrate loading
del model 

NameError: name 'model' is not defined

In [11]:
# Create the evaluation env
env = DummyVecEnv([lambda: BalancebotEnv(render=True)])

In [12]:
# Load the trained agent
model = PPO2.load("ppo_save", env=env, policy=CustomPolicy)





Instructions for updating:
Use keras.layers.flatten instead.


Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where




In [ ]:

# Enjoy trained agent

for ep in range(10):
    obs = env.reset()
    dones = False
    while not dones:
        action, _states = model.predict(obs)
        obs, rewards, dones, info = env.step(action)